In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/dlp-ga-9-image-classification/sample_submission.csv
/kaggle/input/dlp-ga-9-image-classification/test/image_06930.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_07759.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_02911.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_05770.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_00433.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_07838.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_02292.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_06343.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_01971.jpg
/kaggle/input/dlp-ga-9-image-classification/test/image_08741.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_02151.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_02786.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_00342.JPG
/kaggle/input/dlp-ga-9-image-classification/test/image_02257.JPG
/kaggle/input/dlp-ga-9-i

# Importing Libraries

In [2]:
import os
import torch
import matplotlib.pyplot as plt
from torchvision.datasets import ImageFolder
import torchvision.transforms as transforms
from torch.utils.data import DataLoader, random_split
from tqdm import tqdm

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Loading and Augmenting Dataset

In [4]:
train_transforms = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.RandomHorizontalFlip(0.5),
    transforms.RandomCrop(224, padding=4),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

val_transforms = transforms.Compose([
    transforms.Resize(int(224*1.15)),
    transforms.CenterCrop(224),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

In [5]:
data_dir = "/kaggle/input/dlp-ga-9-image-classification"
dataset = ImageFolder(root=data_dir+'/train', transform=train_transforms)
class_names = dataset.classes
print(f"\nFound {len(dataset)} images across {len(class_names)} classes.")


Found 43429 images across 38 classes.


In [6]:
torch.manual_seed(42)

total = len(dataset)
val_len = int(0.2*total)
train_len = total - val_len
train_data, val_data = torch.utils.data.random_split(dataset, [train_len, val_len])
val_data.dataset.transform = val_transforms

# DataLoader

In [7]:
import os
num_cpus = os.cpu_count()
num_cpus

4

In [8]:
batch_size = 64
train_loader = DataLoader(train_data, batch_size=batch_size, shuffle=True, num_workers=num_cpus)
val_loader = DataLoader(val_data, batch_size=batch_size, shuffle=False, num_workers=num_cpus)

dataloaders = {'train': train_loader, 'val': val_loader}
dataset_sizes = {'train': len(train_data), 'val': len(val_data)}

# Set up the Model, Loss Function, and Optimizer


In [9]:
from torchvision.models import resnet50
import torch.nn as nn

model = resnet50(pretrained=True)

# Freeze backbone
for param in model.parameters():
    param.requires_grad = False

# Replace classification head
num_features = model.fc.in_features
model.fc = nn.Linear(num_features, 38)

# Allow training only on the final fc layer
for param in model.fc.parameters():
    param.requires_grad = True

model = model.to(device)

/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:00<00:00, 176MB/s]


**Only the fc layer is optimized.**

In [10]:
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.fc.parameters(), lr=1e-3)

# Training

In [11]:
import torch
import torch.nn as nn
from tqdm import tqdm

def train_model(model, train_loader, val_loader, criterion, optimizer, device, num_epochs=6):

    for epoch in range(num_epochs):

        # ---------------- TRAINING ----------------
        model.train()
        running_loss = 0.0
        running_corrects = 0
        total = 0

        train_pbar = tqdm(train_loader, desc=f"Epoch {epoch+1}/{num_epochs} [Training]", unit="batch", leave=True)

        for images, labels in train_pbar:
            images = images.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            _, preds = torch.max(outputs, 1)
            running_loss += loss.item() * images.size(0)
            running_corrects += torch.sum(preds == labels).item()
            total += labels.size(0)

            # Update postfix with running average loss
            train_pbar.set_postfix(loss=f"{running_loss/total:.4f}", acc=f"{running_corrects/total:.4f}")

        train_loss = running_loss / total
        train_acc = running_corrects / total

        # ---------------- VALIDATION ----------------
        model.eval()
        val_loss = 0.0
        val_corrects = 0
        val_total = 0

        val_pbar = tqdm(val_loader, desc=f"Epoch {epoch+1}/{num_epochs} [Validation]", unit="batch", leave=True)

        with torch.no_grad():
            for images, labels in val_pbar:
                images = images.to(device)
                labels = labels.to(device)

                outputs = model(images)
                loss = criterion(outputs, labels)
                _, preds = torch.max(outputs, 1)

                val_loss += loss.item() * images.size(0)
                val_corrects += torch.sum(preds == labels).item()
                val_total += labels.size(0)

                # Update postfix with running average loss
                val_pbar.set_postfix(loss=f"{val_loss/val_total:.4f}", acc=f"{val_corrects/val_total:.4f}")

        val_loss /= val_total
        val_acc = val_corrects / val_total

        # ---------------- PRINT SUMMARY ----------------
        print(f"Epoch [{epoch+1}/{num_epochs}] "
              f"Train Loss: {train_loss:.4f}  Train Acc: {train_acc:.4f} | "
              f"Val Loss: {val_loss:.4f}  Val Acc: {val_acc:.4f}")


In [12]:
train_model(model, train_loader, val_loader, criterion, optimizer, device, num_epochs=6)

Epoch 1/6 [Validation]: 100%|██████████| 136/136 [00:27<00:00,  4.96batch/s, acc=0.9316, loss=0.2497]


Epoch [1/6] Train Loss: 0.6082  Train Acc: 0.8588 | Val Loss: 0.2497  Val Acc: 0.9316


Epoch 2/6 [Validation]: 100%|██████████| 136/136 [00:29<00:00,  4.62batch/s, acc=0.9482, loss=0.1781]


Epoch [2/6] Train Loss: 0.2112  Train Acc: 0.9411 | Val Loss: 0.1781  Val Acc: 0.9482


Epoch 3/6 [Validation]: 100%|██████████| 136/136 [00:29<00:00,  4.62batch/s, acc=0.9553, loss=0.1500]


...

Epoch [4/6] Train Loss: 0.1355  Train Acc: 0.9594 | Val Loss: 0.1449  Val Acc: 0.9512


Epoch 5/6 [Validation]: 100%|██████████| 136/136 [00:29<00:00,  4.62batch/s, acc=0.9577, loss=0.1301]


Epoch [5/6] Train Loss: 0.1209  Train Acc: 0.9622 | Val Loss: 0.1301  Val Acc: 0.9577


Epoch 6/6 [Validation]: 100%|██████████| 136/136 [00:29<00:00,  4.61batch/s, acc=0.9575, loss=0.1333]

Epoch [6/6] Train Loss: 0.1080  Train Acc: 0.9665 | Val Loss: 0.1333  Val Acc: 0.9575


# Predictions

In [13]:
from pathlib import Path
import pandas as pd
from PIL import Image

def predict_and_save_submission(model, test_dir, class_names, device, output_csv='submission.csv'):
    model.eval()

    test_transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406],
                             std=[0.229, 0.224, 0.225])
    ])

    # Collect test images
    image_paths = sorted([
        p for p in Path(test_dir).glob("*")
        if p.suffix.lower() in [".jpg", ".jpeg", ".png"]
    ])

    predictions = []

    for img_path in image_paths:
        img = Image.open(img_path).convert("RGB")
        img = test_transform(img).unsqueeze(0).to(device)

        with torch.no_grad():
            outputs = model(img)
            _, pred = torch.max(outputs, 1)

        class_idx = pred.item()                    # Already integer label
        class_name = class_names[class_idx]        # Get readable class name
        image_id = img_path.stem                   # File name without extension

        predictions.append((image_id, class_idx))  # Save class index

    # Save submission file
    df = pd.DataFrame(predictions, columns=["Image_ID", "Label"])
    df.to_csv(output_csv, index=False)
    print(df.head())
    print(f"\nSaved submission file to {output_csv}")

    return df

In [14]:
predict_and_save_submission(model, 
                            '/kaggle/input/dlp-ga-9-image-classification/test', 
                            class_names, 
                            device)

      Image_ID  Label
0  image_00001      0
1  image_00002      0
2  image_00003      0
3  image_00004      0
4  image_00005      0

Saved submission file to submission.csv


Image_ID  Label
0      image_00001      0
1      image_00002      0
2      image_00003      0
3      image_00004      0
4      image_00005      0
...            ...    ...
10871  image_10872     37
10872  image_10873     37
10873  image_10874     37
10874  image_10875     34
10875  image_10876     37

[10876 rows x 2 columns]